# Deliverable 3. Create a Travel Itinerary Map

----

1. Create a folder called `Vacation_Itinerary` to store all the files for this deliverable.

2. Download the `Vacation_Itinerary_starter_code.ipynb` file into your `Vacation_Itinerary` folder and rename it `Vacation_Itinerary.ipynb`.

3. Make sure the initial dependencies and the Geoapify API key are imported.

4. From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`.

5. Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

    * The point's size should be the maximum temperature for the city

    * The point's color should be the city's name

    * Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

6. From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

    > **Hint:** You will start and end the route in the same city, so the `vacation_start` and `vacation_end` DataFrames will be in the same city.

7. Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details.

8. Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`.

    > **Hint:** You'll use this DataFrame to create a map using GeoViews, so recall that the first column should be the longitude, and the second the latitude.

9. Use GeoViews to create a map that shows the four cities in the itinerary.

10. Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop.

    > **Hint:** You can note that the `mode` parameter is set to `drive`, you can play around with other modes as it's shown in [the "Travel modes" table](https://apidocs.geoapify.com/docs/routing/#api) in the Geoapify Routing API documentation.

11. Use the Geoapify Routing API to retrieve the route's directions for your itinerary.

12. From the JSON response, store the route's legs coordinates in a variable called `legs`.

13. Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude values into two Python lists named `longitude` and `latitude`.

14. Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`.

15. Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map.

16. Use the asterisk operator to display a composed plot that shows the itinerary's route over the map containing the cities. 

17. Save your map to the `Vacation_Itinerary` folder as `WeatherPy_travel_map.png`.

---

## Make sure the initial dependencies and the Geoapify API key are imported

In [1]:
# Dependencies and Setup
import geoviews as gv
import hvplot.pandas
import pandas as pd
import requests

# Turn off warning messages
import warnings
warnings.filterwarnings("ignore")

# Import API key
from config import geoapify_key

## From your `Vacation_Search` folder from Deliverable 2, import the `WeatherPy_vacation.csv` file as a DataFrame named `vacation_df`

In [2]:
# Read the WeatherPy_vacation.csv into a DataFrame
import os
file_to_load = os.path.join('..', 'vacation_search','weatherpy_vacation.csv')
vacation_df = pd.read_csv(file_to_load)

# Display sample data
vacation_df

City Country  Max Temp Current Description      Lat       Lng  \
0       Rikitea      PF     25.28           clear sky -23.1203 -134.9692   
1      Hermanus      ZA     24.89           clear sky -34.4187   19.2345   
2          Hilo      US     20.14     overcast clouds  19.7297 -155.0900   
3        Castro      BR     20.89     overcast clouds -24.7911  -50.0119   
4      Saldanha      ZA     25.03          few clouds -33.0117   17.9442   
..          ...     ...       ...                 ...      ...       ...   
117  Bluefields      NI     26.12    scattered clouds  12.0137  -83.7635   
118      Ambulu      ID     24.78     overcast clouds  -8.3450  113.6058   
119     Isangel      VU     25.48          few clouds -19.5500  169.2667   
120       Jambi      ID     23.54     overcast clouds  -1.6000  103.6167   
121     Villeta      CO     29.34     overcast clouds   5.0089  -74.4723   

                  Hotel Name  
0       Chez Bianca & Benoit  
1           Aloe guest house  
2          Dolphin Bay Hotel  
3       Hotel Central Palace  
4                Hoedjesbaai  
..                       ...  
117             Hotel Isleño  
118             Hotel Ambulu  
119              Tanna Lodge  
120  Hotel Odua Weston Jambi  
121       Hotel Mediterraneo  

[122 rows x 7 columns]

## Use GeoViews to create a map that shows all the cities in the `vacation_df` DataFrame. Configure the map as follows:

* The point's size should be the maximum temperature for the city

* The point's color should be the city's name

* Use the `hover_cols` parameter to the the "Hotel Name", "Country", and "Current Description" columns to each point as additional information.

In [3]:
# Configure the map plot
map_plot = vacation_df.hvplot.points(
    "Lng",
    "Lat",
    geo=True,
    tiles="OSM",
    color="City",
    alpha=0.6,
    size="Max Temp",
    scale= 1.5,
    frame_width = 700,
    frame_height = 500,
    hover_cols = ["Hotel Name", "Country", "Current Description"]

)

# Display the map
map_plot

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Hotel Name,Country,Current Description)

## From the map, *choose four cities* that a customer might want to visit. They should be close together and in the same country. Use the `loc` method to create separate DataFrames for each city on the travel route.

In [4]:
# Create DataFrames for each city by filtering the 'vacation_df' using the loc method

vacation_start = vacation_df.loc[vacation_df['City'] == "Sibolga"]
vacation_end = vacation_start
vacation_stop1 = vacation_df.loc[vacation_df['City'] == "Jambi"]
vacation_stop2 = vacation_df.loc[vacation_df['City'] == "Bengkulu"]
vacation_stop3 = vacation_df.loc[vacation_df['City'] == "Padang"]

## Use the Pandas `concat` function to merge the DataFrame from each city in the itinerary to create a new DataFrame named `itinerary_df` to store the itinerary details

In [5]:
# Use the Pandas concat function to create a new DataFrame to store the itinerary details.
itinerary_df = pd.concat([vacation_start, vacation_stop1, vacation_stop2, vacation_stop3, vacation_end])
itinerary_df.index.name = "City ID"
itinerary_df = itinerary_df.reset_index()

# Display sample data
itinerary_df

City ID      City Country  Max Temp Current Description     Lat       Lng  \
0       16   Sibolga      ID     24.75          light rain  1.7427   98.7792   
1      120     Jambi      ID     23.54     overcast clouds -1.6000  103.6167   
2       24  Bengkulu      ID     24.76     overcast clouds -3.8004  102.2655   
3       11    Padang      ID     25.03          light rain -0.9492  100.3543   
4       16   Sibolga      ID     24.75          light rain  1.7427   98.7792   

                Hotel Name  
0        Hotel Prima Indah  
1  Hotel Odua Weston Jambi  
2               Dena Hotel  
3             losmen Surya  
4        Hotel Prima Indah

## Use the Pandas `copy` function to create a new DataFrame named `waypoints_df` to store the longitude and latitude for each city in `itinerary_df`

In [6]:
# Create a Pandas DataFrame to store the latitude and longitude for each city in the itinerary
waypoints_df = itinerary_df[["Lng","Lat"]].copy()
# Display sample data
waypoints_df

Lng     Lat
0   98.7792  1.7427
1  103.6167 -1.6000
2  102.2655 -3.8004
3  100.3543 -0.9492
4   98.7792  1.7427

## Use GeoViews to create map that shows the four cities in the itinerary

In [7]:
# Configure the map plot by using the itinerary_df
waypoints_map = itinerary_df.hvplot.points(
    "Lng",
    "Lat",
    geo=True,
    tiles="OSM",
    frame_width= 700,
    frame_height= 500,
    color="City",
    alpha=0.7,
    size= "Max Temp",
    scale= 4,
    hover_cols = ["Hotel Name", "Country", "Current Description"]
)

In [8]:
# Display the route_map
waypoints_map

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Hotel Name,Country,Current Description)

## Next, you'll use the Geoapify Routing API to find a route between the cities in the itinerary. Review the code that sets the initial parameters and fetches the coordinates from each city to define the `waypoints` parameter by using a `for` loop

In [9]:
# Set parameters to trace the route
radius = 5000
params = {
    "mode":"drive",
    "apiKey": geoapify_key,
}

In [10]:
# Set an empty waypoints String variable
waypoints = ""

# Iterate through the route_df DataFrame to define the waypoints
for index, row in waypoints_df.iterrows():
    waypoints = waypoints + str(row["Lat"]) + "," + str(row["Lng"]) + "|"

# Delete the last character from the string
waypoints = waypoints[:-1]

# Add the waypoints to the params dictionary
params["waypoints"] = waypoints

# Display the params dictionary
# params

## Use the Geoapify Routing API to retrieve the route's directions for your itinerary

In [11]:
# Set up the base URL for the Geoapify Places API.
base_url = "https://api.geoapify.com/v1/routing"

# Make request and retrieve the JSON data by using the params dictionary
route_response = requests.get(base_url, params=params)

# Convert the API response to JSON format
route_response = route_response.json()

## From the JSON response, store the route's legs coordinates in a variable called `legs`

In [12]:
# Fetch the route's legs coordinates from the JSON response
legs = route_response["features"][0]["geometry"]["coordinates"]

## Loop through the route legs coordinates to fetch the latitude and longitude for each step. Store the latitude and longitude value into two Python lists names `longitude` and `latitude`

In [13]:
# Create and empty list to store the longitude of each step
lng_list = []

# Create and empty list to store the latitude of each step
lat_list = []

# Loop through the legs coordinates to fetch the latitude and longitude for each step
for leg in legs:
    for coordinates in leg:
        lng_list.append(coordinates[0])
        lat_list.append(coordinates[1])

## Use the `longitude` and `latitude` Python lists to create a new DataFrame named `route_df`

In [14]:
# Create an empty DataFrame to store the steps' coordinates
route_df = pd.DataFrame()

# Add the steps' longitude and latitude from each step as columns to the DataFrame
route_df["Lng"] = lng_list
route_df["Lat"] = lat_list

# Display sample data
route_df

Lng       Lat
0      98.779042  1.743144
1      98.779656  1.743362
2      98.780072  1.742491
3      98.780103  1.742434
4      98.780140  1.742379
...          ...       ...
69879  98.780140  1.742379
69880  98.780103  1.742434
69881  98.780072  1.742491
69882  98.779656  1.743362
69883  98.779042  1.743144

[69884 rows x 2 columns]

##  Use the GeoViews `Path` function to configure a line plot by using `route_df`. Set a custom color and width for the line that may contrast with the map

In [15]:
# Configure the route path by using the GeoViews' Path function
route_path = gv.Path(route_df)

In [16]:
# Display a composed plot by using the route_map and route_path objects
waypoints_map * route_path.options(color= "red", line_width=3)

:Overlay
   .Tiles.I  :Tiles   [x,y]
   .Points.I :Points   [Lng,Lat]   (City,Max Temp,Hotel Name,Country,Current Description)
   .Path.I   :Path   [Lng,Lat]